**AutoML OSS入門（2）**

# 4行でモデル構築と予測が表示できるAutoML OSSの老舗「auto-sklearn」を解説

本ノートブックの紹介記事と合わせてごらんください。
- ＠IT連載 AutoML OSS入門（２）- 第2回「4行でモデル構築と予測が表示できるAutoML OSSの老舗「auto-sklearn」を解説」

また、ノートブックの扱い方やタイタニックの生存予測データについては、連載記事の第1回も参照してください。
- [＠IT連載 AutoML OSS入門（１）- 第1回「機械学習モデル構築作業の煩雑さを解消する「AutoML」とは――歴史、動向、利用のメリットを整理する」](https://www.atmarkit.co.jp/ait/articles/2107/02/news006.html)

## タイタニックデータでAutoML
タイタニックの生存予測データを使って、auto-sklearnを紹介していきます。



### セットアップ
auto-sklearnをインストールします。


In [ ]:
# 依存するパッケージのインストール
!curl https://raw.githubusercontent.com/automl/auto-sklearn/master/requirements.txt | xargs -n 1 -L 1 pip install

# auto-sklearnのインストール
!pip install auto-sklearn

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100   209  100   209    0     0   1866      0 --:--:-- --:--:-- --:--:--  1866
     |████████████████████████████████| 22.3MB 68.3MB/s 
  Found existing installation: scikit-learn 0.22.2.post1
    Uninstalling scikit-learn-0.22.2.post1:
      Successfully uninstalled scikit-learn-0.22.2.post1
     |████████████████████████████████| 727kB 34.2MB/s 
     |████████████████████████████████| 983kB 48.5MB/s 
     |████████████████████████████████| 122kB 55.2MB/s 
  Found existing installation: cloudpickle 1.3.0
    Uninstalling cloudpickle-1.3.0:
      Successfully uninstalled cloudpickle-1.3.0
  Found existing installation: dask 2.12.0
    Uninstalling dask-2.12.0:
      Successfully uninstalled dask-2.12.0
  Found existing installation: distributed 1.25.3
    Uninstalling distributed-1.25.3:
      Successfully uninstalled distributed-

(注) ランタイムを再起動してください。
- ランタイムの再起動方法<br>
ランタイム > ランタイムを再起動 を実行

In [ ]:
# auto-sklearnのインストール確認
# バージョンが表示されればOK!!
import autosklearn
print(autosklearn.__version__)

0.12.6


### データのロード
タイタニックの生存予測データをダウンロードし、データを読み込みます。<br>
第1回記事の「タイタニックの生存予測データの取得方法と解説」を参照してください。

In [ ]:
# データの準備
!wget -N https://github.com/aiq2020-tw/automl-notebooks/raw/main/titanic.zip
!unzip titanic.zip

--2021-07-08 22:55:55--  https://github.com/aiq2020-tw/automl-notebooks/raw/main/titanic.zip
Resolving github.com (github.com)... 140.82.112.4
Connecting to github.com (github.com)|140.82.112.4|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/aiq2020-tw/automl-notebooks/main/titanic.zip [following]
--2021-07-08 22:55:55--  https://raw.githubusercontent.com/aiq2020-tw/automl-notebooks/main/titanic.zip
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 34877 (34K) [application/zip]
Saving to: ‘titanic.zip’

titanic.zip         100%[===================>]  34.06K  --.-KB/s    in 0.001s  

Last-modified header missing -- time-stamps turned off.
2021-07-08 22:55:55 (47.4 MB/s) - ‘titanic.zip’ saved [3487

In [ ]:
# 学習データ/テストデータの読み込み
import pandas as pd

train_df = pd.read_csv('train.csv')
print('Train data shape:', str(train_df.shape))
test_df = pd.read_csv('test.csv')
print('Test data shape:', str(test_df.shape))

Train data shape: (891, 12)
Test data shape: (418, 11)


### データの前処理
データを説明変数と目的変数に分けます。<br>
また、カテゴリカル変数は数値変数に変換します。

In [ ]:
# 目的変数
y_train = train_df.pop('Survived')
# 説明変数（PassengerIdは除去）
X_train = train_df.drop(['PassengerId'], axis=1)
X_test = test_df.drop('PassengerId', axis=1)

In [ ]:
# データタイプ確認
X_train.dtypes

Pclass        int64
Name         object
Sex          object
Age         float64
SibSp         int64
Parch         int64
Ticket       object
Fare        float64
Cabin        object
Embarked     object
dtype: object

In [ ]:
# カテゴリカル変数を数値変数に変換
# 注) 本来カテゴリカル変数にはタイプとして「category」を設定すべきだが、今回は未設定。
from sklearn.preprocessing import LabelEncoder

list_cols = ['Name', 'Sex', 'Ticket', 'Cabin', 'Embarked']
for col in list_cols:
    target_column = pd.concat([X_train[col], X_test[col]])
    le = LabelEncoder()
    le.fit(target_column)
    X_train[col] = le.transform(X_train[col])
    # X_train[col] = X_train[col].astype('category')
    X_test[col] = le.transform(X_test[col])
    # X_test[col] = X_test[col].astype('category')
X_train.dtypes

Pclass        int64
Name          int64
Sex           int64
Age         float64
SibSp         int64
Parch         int64
Ticket        int64
Fare        float64
Cabin         int64
Embarked      int64
dtype: object

### モデルの学習
`AutoSklearnClassifier`クラスを使ってモデルを学習します。

In [ ]:
from autosklearn.classification import AutoSklearnClassifier

# モデルのインスタンス生成
cls = AutoSklearnClassifier(time_left_for_this_task=120, seed=42)
# モデルの学習
cls.fit(X_train, y_train)

AutoSklearnClassifier(per_run_time_limit=12, seed=42,
                      time_left_for_this_task=120)

In [ ]:
# 学習済みモデルの情報
print(cls.sprint_statistics())
print(cls.show_models())

auto-sklearn results:
  Dataset name: bd9c1a18-e03f-11eb-818a-0242ac1c0002
  Metric: accuracy
  Best validation score: 0.827119
  Number of target algorithm runs: 32
  Number of successful target algorithm runs: 30
  Number of crashed target algorithm runs: 0
  Number of target algorithms that exceeded the time limit: 2
  Number of target algorithms that exceeded the memory limit: 0

[(0.460000, SimpleClassificationPipeline({'balancing:strategy': 'none', 'classifier:__choice__': 'adaboost', 'data_preprocessing:categorical_transformer:categorical_encoding:__choice__': 'one_hot_encoding', 'data_preprocessing:categorical_transformer:category_coalescence:__choice__': 'minority_coalescer', 'data_preprocessing:numerical_transformer:imputation:strategy': 'mean', 'data_preprocessing:numerical_transformer:rescaling:__choice__': 'robust_scaler', 'feature_preprocessor:__choice__': 'extra_trees_preproc_for_classification', 'classifier:adaboost:algorithm': 'SAMME.R', 'classifier:adaboost:learning_r

### テストデータの予測
テストデータを予測して、Kaggleへの提出ファイルを作成します。

In [ ]:
# 予測
test_df['Survived'] = cls.predict(X_test)
# csvファイル作成
test_df[['PassengerId','Survived']].to_csv('submission.csv', index=None)

## その他の機能と応用
可視化ツールのPipelineProfilerとauto-sklearn 2.0を紹介します。

### PipelineProfiler
PipelineProfilerツールを使用して、学習済みモデルの内部情報を可視化してみましょう。

In [ ]:
!pip install pipelineprofiler

     |████████████████████████████████| 880kB 31.2MB/s 


In [ ]:
import PipelineProfiler
profiler_data = PipelineProfiler.import_autosklearn(cls)
PipelineProfiler.plot_pipeline_matrix(profiler_data)

出力結果をマウス操作することで、学習済みモデルの内部情報を確認することができます。<br>
いくつか機能を紹介します。
- パイプライン(例として auto-sklearn #1)上のプリミティブタイプにマウスオーバーすると、その処理のタイプやハイパーパラメーターなどの情報を確認できる。
- 上部の前処理や分類器等をクリックすると、ハイパーパラメーターとその値が表示される。
- パイプラインをマウスで選択すると、パイプラインの構造が表示される。
- 「ACCURACY」をクリックして「ENSEMBLE WEIGHT」などを選択すると、選択された条件でパイプラインを並び替えられる。

### auto-sklearn 2.0
auto-sklearn 2.0で同様にモデルを学習し、予測を行ってみましょう。使い方は同じです。

In [ ]:
from autosklearn.experimental.askl2 import AutoSklearn2Classifier

# 学習
cls2 = AutoSklearn2Classifier(time_left_for_this_task=120, seed=42)
cls2.fit(X_train, y_train)
# 予測
test_df['V2_Survived'] = cls2.predict(X_test)

Using no backup selector


以上で、タイタニックの生存予測データを使ったauto-sklearnの紹介は終わりです。